In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation

from scipy.fftpack import fft, ifft, fftfreq, dst
import scipy.integrate as integ
import scipy.linalg as la

# Ecuación de ondas

Vamos a estudiar distintas formas de resolver la ecuación de ondas. Las técnicas que vamos a estudiar sirven para otras ecuaciones, y para otros enfoques, como podéis leer más despacio en estas referencias:

 - Leo M. González, Fabricio Macià, Antonio Souto Iglesias: Estabilidad, aproximación numérica y mecánica de fluidos
 - J.M. Sanz-Serna: Fourier Techniques in Numerical Methods for Evolutionary Problems



Comenzamos con una cuerda vibrante en una cierta posición inicial.
Para simplificar, tomaremos la velocidad inicial igual a cero, y las condiciones de contorno corresponden a los dos extremos fijos. Entre los exámenes y prácticas de otros cursos podrás encontrar más variantes, y si necesitas alguna otra, puedes consultar a los profesores.

Cuando hayas terminado de recorrer el cuaderno, te recomendamos que pruebes a cambiar el perfil inicial.

In [ ]:
L = 1
x1,x2,x3 = 0.4,0.5,0.6
def init_fn(x):
    return np.exp(-((x-0.5)**2)/0.01)
#    return np.sin(np.pi*x/L)
#    return x*(1-x)
#    #Función definida "a trozos"
#    return np.piecewise(x,
#        [(x>=x1)&(x<x2),(x>=x2)&(x<x3)],
#        [lambda y:(y-x1)/(x2-x1),lambda y:(x3-y)/(x3-x2), 0])

xs = np.linspace(0,L,200)
us = init_fn(xs)
plt.plot(xs, us)
plt.xlabel('x')
plt.ylabel('u')
plt.title('initial position of the string (initial speed is zero)')

## Serie de senos

Comenzamos por recordar la __serie de senos__ de una función f.

Una función $f:[0,L]\rightarrow\mathbb{R}$ tal que $f(0)=f(L)=0$ se puede escribir como suma de una _serie de senos_
$$
f(x)=\sum_{k=1}^\infty \hat{f}_k \sin\left(\frac{\pi k}{l}x\right)
$$
donde
$$
\hat{f}_k = \frac{2}{L}\int_0^L f(x)\sin\left(\frac{\pi k}{l}x\right)\: d x
$$

In [ ]:
f = init_fn

#Primeros coeficientes de la serie de senos de f
for k in range(1,6):
    integral, error = integ.quad(lambda x : 2./L * f(x)*np.sin(np.pi*k*x), 0., L )
    print(k, integral)

## Discrete sine transform

El algoritmo __FFT__ (Fast Fourier Transform) es una forma muy eficiente de aproximar los coeficientes de la serie de Fourier.

La __discrete sine transform__ es una versión discreta de la serie de senos, análoga a la DFT (Discrete Fourier Transform) para la transformada de Fourier.

En general no se usa en tratamiento de señales, como la transformada de Fourier, pero es útil precisamente para resolver ecuaciones en derivadas parciales por técnicas espectrales.

In [ ]:
# Aproximamos los primeros coeficientes de la serie de senos de f
# mediante la dst
# Compara con los valores obtenidos antes
N = 20
h = L/(N+1)
xs = np.linspace(h, L-h, N)
fs = f(xs)
Xk = dst(fs)*(L/(N+1))
Xk[:6]

In [ ]:
# Aproximamos los los primeros coeficientes de la serie de senos de f
# mediante la dst
N  = 20
h  = L/(N+1)
xs = np.linspace(h, L-h, N)
fs = f(xs)
Xk = dst(fs)*(L/(N+1))

#Dibujamos los Coeficientes de la serie de senos
plt.plot(Xk[:20],'go', label='coeficientes')
plt.legend()
plt.title('Coeficientes de la serie de senos')

#Dibujamos la función f
plt.figure()
x_eval = np.linspace(0, L, 200)
f_eval = f(x_eval)
plt.plot(x_eval,f_eval, label='f')

#reconstrucción de la función mediante su serie de senos truncada
senos = np.zeros_like(x_eval)
for k in range(N):
    onda      = lambda x: np.sin((np.pi*(k+1)/L)*x)
    onda_eval = onda(x_eval)
    senos     = senos + Xk[k]*onda_eval

plt.plot(x_eval, senos, 'g-', label='Serie de senos hasta grado %d'%N)
plt.title('Reconstrucción con la serie de senos')
plt.legend()

Al sumar sólo algunos de los términos de la serie, tenemos una aproximación a la función $f$:

$$
f(x)\approx\sum_{k=1}^N \hat{f}_k \sin\left(\frac{\pi k}{l}x\right)
$$

In [ ]:
# Dibujamos las sumas parciales de la serie de senos...
f = init_fn
N = 12
h = L/(N+1)
xs = np.linspace(h, L-h, N)
fs = f(xs)
Xk = dst(fs)*(L/(N+1))

plt.figure(figsize=(12,8))
plt.plot(x_eval, f_eval, label='f')

senos = np.zeros_like(x_eval)
for k in range(N):
    onda = lambda x: np.sin((np.pi*(k+1)/L)*x)
    onda_eval = onda(x_eval)
    senos     = senos + Xk[k]*onda_eval
    plt.plot(x_eval, senos, label='serie de senos hasta N=%d'%(k+1))

plt.xlabel('x')
plt.ylabel('u')
plt.title('aproximaciones con la serie de senos')
plt.legend()

### Ejercicio

 - Aproxima con series de senos otras funciones similares pero que no sean diferenciables: ¿empeora mucho la calidad de la aproximación?

## Método espectral

Queremos resolver la ecuación de la cuerda vibrante:
$$
\partial_{tt}u = c^2\partial_{xx}u.
$$

Es equivalente a escribir:
$$
\frac{\partial^2u}{\partial t^2}(t,x) = c^2\frac{\partial^2u}{\partial x^2}(t,x).
$$

Para cada $t$ fijo, descomponemos la función u en su serie de senos, en la variable $x$:
$$
u(t,x)=\sum_{k=1}^\infty \hat{u}_k(t) \sin\left(\frac{\pi k}{l}x\right)
$$
Sustituyendo esta expresión en la ecuación obtenemos:
$$
\partial_{tt}\left(\sum_{k=1}^\infty \hat{u}_k(t) \sin\left(\frac{\pi k}{l}x\right)\right)
=c^2\partial_{xx}\left(\sum_{k=1}^\infty \hat{u}_k(t) \sin\left(\frac{\pi k}{l}x\right)\right)
$$
Es decir:
$$
\sum_{k=1}^\infty \partial_{tt}\hat{u}_k(t) \sin\left(\frac{\pi k}{l}x\right)
=\sum_{k=1}^\infty \hat{u}_k(t) c^2\partial_{xx}\sin\left(\frac{\pi k}{l}x\right)
=\sum_{k=1}^\infty \hat{u}_k(t) \left(-\left(\frac{\pi c k}{l}\right)^2\right)\sin\left(\frac{\pi k}{l}x\right)
$$
y como los coeficientes de la serie de senos son únicos, tenemos que, para cada $k$:
$$
\partial_{tt}\hat{u}_k(t) = -\left(\frac{\pi c k}{l}\right)^2\hat{u}_k(t) 
$$

Estas ecuaciones son fáciles de resolver.
La solución de 
$\partial_{tt}\hat{u}_k(t) = -\left(\frac{\pi c k}{l}\right)^2\hat{u}_k(t) $ con $u(0)=u_0$ y $u'(0)=v_0$ es
$$
\hat{u}_k(t) = u_0\cos\left(\frac{\pi c k}{l}t\right) + v_0\sin\left(\frac{\pi c k}{l}t\right)
$$


Como dijimos, asumimos que la velocidad inicial es 0.
Escribimos la posición inicial de la cuerda $f$ como serie de senos:
$$
f(x)=\sum_{k=1}^\infty \hat{f}_k \sin\left(\frac{\pi c k}{l}x\right)
$$
y deducimos que la solución del problema:
$$
\begin{array}{rcl}
\partial_{tt}u &=& \partial_{xx}u\\
u(0,x)&=&f(x)\\
\partial_t u(0,x)&=&0\\
u(t,0)&=&0\\
u(t,l)&=&0
\end{array}
$$
tiene la forma:
$$
u(t,x)=\sum_{k=1}^\infty \hat{f}_k\cos\left(\frac{\pi c k}{l}t\right) \sin\left(\frac{\pi c k}{l}x\right)
$$

Usando la fórmula para el producto de $\sin$ y $\cos$ obtenemos:
$$
u(t,x)=\sum_{k=1}^\infty \hat{f}_k\left(\sin\left(\frac{\pi c k}{l}t+\frac{\pi c k}{l}x\right)+\sin\left(\frac{\pi c k}{l}t-\frac{\pi c k}{l}x\right)\right) 
$$
Es decir, la solución es suma de ondas viajeras.

In [ ]:
t0, tf = 0,1

Dibujamos la posición de la cuerda en varios instantes del intervalo $[0,1]$.

In [ ]:
N = 100
h = L/(N+1)
xs = np.linspace(h, L-h, N)
fs = f(xs)
Xk = dst(fs)*(L/(N+1))

#reconstrucción
for t in np.linspace(t0, 1, 6):
    fourier = np.zeros_like(x_eval)
    for k in range(N):
        onda = lambda x: np.sin((np.pi*(k+1)/L)*x)
        onda_eval = onda(x_eval)
        fourier = fourier + Xk[k]*np.cos(np.pi*(k+1)*t/L)*onda_eval
    plt.plot(x_eval, fourier, label='t=%.3f'%t)

plt.title('Ondas, solución exacta (pero truncada)')
plt.xlabel('x')
plt.ylabel('u')
plt.legend()

Como curiosidad, generamos una animación, que queda guardad en un fichero `wave.mp4`.

In [ ]:
fig  = plt.figure()
plts = []             # get ready to populate this list the Line artists to be plotted

for t in np.linspace(t0, 1, 100):
    fourier = np.zeros_like(x_eval)
    for k in range(N):
        onda      = lambda x: np.sin((np.pi*(k+1)/L)*x)
        onda_eval = onda(x_eval)
        fourier   = fourier + Xk[k]*np.cos(np.pi*(k+1)*t/L)*onda_eval
    p, = plt.plot(x_eval, fourier, 'k', label='t=%.3f'%t)
    plts.append( [p] )           # ... but save the line artist for the animation
    
ani = matplotlib.animation.ArtistAnimation(fig, plts, interval=50, repeat_delay=3000)   # run the animation
ani.save('wave.mp4')    # optionally save it to a file
plt.show()

## Discretización espacial, solución temporal exacta

Comparamos ahora con otro enfoque: Reemplazamos la función inicial $u$ de una variable real por un vector con los valores de $u$ en los puntos de un mallado:

$$
\overrightarrow{u}=\left(u(x_1),\dots,u(x_j),\dots,u(x_{n-1})\right),\quad
x_j=x_0+j\cdot h
$$
Observa que no incluimos $u(x_0)$ ni $u(x_n)$, porque son siempre 0 por definición.

Reemplazamos la ecuación en derivadas parciales (con $c=1$):
$$
\partial_{tt}u = \partial_{xx}u
$$
por la siguiente ecuación diferencial ordinaria
$$
\partial_{tt}\overrightarrow{u} = D\cdot \overrightarrow{u}
$$
donde $D$ es un operador de diferencias finitas (que aprovecha que $u(x_0)=u(x_n)=0$):
$$
D\cdot \overrightarrow{u}=\left(\frac{2u(x_1)-u(x_{2})}{h^2},
\frac{-u(x_{1})+2u(x_2)-u(x_{3})}{h^2},
\dots,
\frac{-u(x_{j-1})+2u(x_j)-u(x_{j+1})}{h^2},\dots\right)
$$

La matriz $D$ es una vieja conocida:
$$D=\frac{1}{h^2}\left(\begin{array}{rrrrr}
2.0 & -1.0 & 0.0 & 0.0 & 0.0 \\
-1.0 & 2.0 & -1.0 & 0.0 & 0.0 \\
0.0 & -1.0 & 2.0 & -1.0 & 0.0 \\
0.0 & 0.0 & -1.0 & 2.0 & -1.0 \\
0.0 & 0.0 & 0.0 & -1.0 & 2.0
\end{array}\right)$$

In [ ]:
def diff_fin_matrix(n):
    return np.diag(2*np.ones(n)) - np.diag(np.ones(n-1),1) - np.diag(np.ones(n-1),-1)

D = diff_fin_matrix(5)
print(D)

Este sistema de EDOs se puede resolver de forma exacta.
El primer paso es expresarlo como un sistema de primer orden:
$$
\frac{\partial}{\partial t}
\left(
\begin{array}{c}
\overrightarrow{u}\\
\overrightarrow{v}
\end{array} \right)=
\left(
\begin{array}{c|c}
\mathbf{0}&\mathbf{Id}\\
\hline
D&\mathbf{0}
\end{array}
\right)\cdot
\left(
\begin{array}{c}
\overrightarrow{u}\\
\overrightarrow{v}
\end{array}
\right)$$
Llamamos a esta matriz 
$$
C = \left(
\begin{array}{c|c}
\mathbf{0}&\mathbf{Id}\\
\hline
D&\mathbf{0}
\end{array}
\right)
$$
y la solución es:
$$
\left(
\begin{array}{c}
\overrightarrow{u}(t)\\
\overrightarrow{v}(t)
\end{array} \right)=
e^{t\cdot C}\cdot \left(
\begin{array}{c}
\overrightarrow{u}(0)\\
\overrightarrow{v}(0)
\end{array} \right)
$$

In [ ]:
L  = 1
Nx = 50
h  = L/Nx

t0 = 0
tf = 1

xs = np.linspace(0, L , Nx+1)
xs_int = xs[1:-1]
u0 = init_fn(xs_int)
v0 = np.zeros((Nx-1,))
uv0 = np.concatenate([u0,v0])

C = np.zeros((2*(Nx-1),2*(Nx-1)))
C[Nx-1:,:Nx-1] = -(1/h**2)*diff_fin_matrix(Nx-1)
C[:Nx-1,Nx-1:] = np.eye(Nx-1)

plt.figure(figsize=(8,8))
for t in np.linspace(t0, tf, 6):
    uv_t = la.expm(t*C)@uv0
#   print(uv_t)
    u_t = np.zeros(Nx+1)
    u_t[1:-1] = uv_t[:Nx-1]
    plt.plot(xs, u_t, label='t=%.3f'%t)

plt.legend()
plt.xlabel('x')
plt.ylabel('u')
plt.title('Integración temporal exacta del problema espacial discretizado')

### Ejercicio (Método adaptativo de Runge-Kutta 4,5)

Resuelve el sistema de EDOs anterior usando el método adaptativo de Runge-Kutta (4,5), llamando al método `solve_ivp` de `scipy.integrate`.

# Ecuación de ondas con diferencias finitas

Ya que hemos reemplazado la derivada espacial por una aproximación numérica, tiene sentido intentar reemplazar también la derivada temporal por una regla de derivación numérica. Esta técnica se conoce como __diferencias finitas__.

Como el tiempo avanza desde la solución inicial y hemos definido $v=u_t$, podemos aproximar la derivada $u_{tt}$ así:

$$
\partial_{t}u(t_{j},x) = v(t_j, x)
$$
$$
\partial_{tt}u(t_{j},x)\approx \frac{u_t(t_{j+1},x) - u_t(t_j,x)}{k} 
= \frac{v(t_{j+1},x) - v(t_j,x)}{k}
$$
para un _paso temporal $k$_. Ésto nos permite avanzar en el tiempo de esta forma:
$$
\begin{array}{lcl}
\overrightarrow{u}_{j+1} &=& \overrightarrow{u}_j + k \overrightarrow{v}_j\\
\overrightarrow{v}_{j+1} &=& \overrightarrow{v}_j + k D\cdot \overrightarrow{u}_j
\end{array}
$$



Usar la técnica de diferencias finitas anterior es equivalente a usar un método de Euler para integrar el sistema de primer orden:
$$
\frac{\partial}{\partial t}
\left(
\begin{array}{c}
\overrightarrow{u}\\
\overrightarrow{v}
\end{array} \right)=
\left(
\begin{array}{c|c}
\mathbf{0}&\mathbf{Id}\\
\hline
D&\mathbf{0}
\end{array}
\right)\cdot
\left(
\begin{array}{c}
\overrightarrow{u}\\
\overrightarrow{v}
\end{array}
\right)$$

In [ ]:
L  = 1
Nx = 100
h  = L/Nx

t0 = 0
tf = 1
Nt = 700
k  = (tf - t0)/Nt

lamb = k/h

xs = np.linspace(0, L , Nx+1)
xs_int = xs[1:-1]
u0 = init_fn(xs_int)
v0 = np.zeros((Nx-1,))

A = -(1/h**2)*diff_fin_matrix(Nx-1)
u = np.zeros((Nt+1,Nx+1)) #solution to WE
u[0,1:-1] = u0
vt = v0
for j in range(Nt):
    ut_int = u[j,1:-1]
    u_new = ut_int + k*vt
    vt = vt + k*A@ut_int
    u[j+1,1:-1] = u_new

for t in np.linspace(0, Nt-1, 6):
    plt.plot(u[int(t),:], label='t=%.3f'%(t*k))
plt.legend()
plt.xlabel('x')
plt.ylabel('u')
plt.title('Integración temporal con Euler del problema espacial discretizado')

### Ejercicio

Observa que para Nx=100 divisiones espaciales y Nt = 700 divisiones espaciales, aparecen oscilaciones al final del intervalo temporal. Comprueba que con un intervalo de tiempo un poco mayor o unas pocas divisiones espaciales más, las oscilaciones crecen de forma exponencial.

# Diferencia temporal de segundo orden

Es más habitual usar una diferencia centrada de segundo orden para aproximar la derivada temporal, ya que hemos usado una diferencia centrada para aproximar la derivada espacial:
$$
\partial_{tt}u(t_{j},x)\approx \frac{u(t_{j+1},x) - 2u(t_j,x) +u(t_{j-1},x)}{k^2}
$$
Observa que es necesario hacer un apaño para dar el primer paso desde la posición inicial, porque necesitamos los dos últimos pasos para dar el paso siguiente.

In [ ]:
L  = 1
Nx = 100
h  = L/Nx

t0 = 0
tf = 1
Nt = 100
k = (tf - t0)/Nt

c = 1.0
lamb2 = c*(k/h)**2

xs = np.linspace(0, L, Nx+1)
xs_int = xs[1:-1]
u0 = init_fn(xs_int)
u = np.zeros((Nt+1,Nx+1))
u[0,1:-1] = u0
# El primer paso temporal es un poco delicado
# mas detalles en la seccion 12.3 del Burden Faires
# "Improving the Initial Approximation"

for a in range(1, Nx-1):
    u[1,a] = (1-lamb2)*u[0,a] + (lamb2/2)*(u[0,a-1]+u[0,a+1])

#El resto de pasos temporales siguen el mismo patron
for j in range(1, Nt):
    for a in range(1, Nx-1):
        u[j+1,a] = 2*(1-lamb2)*u[j,a]-u[j-1,a]+lamb2*(u[j,a-1]+u[j,a+1])

for t in np.linspace(0, Nt-1, 6):
    plt.plot(u[int(t),:], label='t=%.3f'%(t*k))
    
plt.legend()
plt.xlabel('x')
plt.ylabel('u')
plt.title('Integración temporal de segundo orden del problema espacial discretizado')

Usar una diferencia temporal de orden 2 no evita necesariamente la inestabilidad que observamos con el método de Euler.

Al aplicar este método a la ecuación de ondas
$$
\partial_{tt}u = c^2\partial_{xx}u,
$$
con un paso espacial $h$ y un paso temporal $k$, la __condición de estabilidad de Courant__ se define así:
$$
\frac{ck}{h}<1.
$$
La condición de estabilidad es necesaria para que el método converja. Es la misma que aparece en la ecuación de transporte, porque están muy relacionadas. La ecuación de ondas se puede factorizar como dos ecuaciones de transporte:
$$
{\displaystyle \left[{\frac {\partial }{\partial t}}-c{\frac {\partial }{\partial x}}\right]\left[{\frac {\partial }{\partial t}}+c{\frac {\partial }{\partial x}}\right]u=0.\,}
$$
lo que da lugar a la [fórmula de D'Alembert](https://es.wikipedia.org/wiki/F%C3%B3rmula_de_d%27Alembert)

### Ejercicio

Prueba a cambiar el intervalo temporal, el número de divisiones espaciales y temporales, de modo que la condición de estabilidad no se cumpla, pero por un margen estrecho (por ejemplo $1<\frac{ck}{h}<2$), y observa si la solución es estable.

### Ejercicio opcional

Para el método de Euler usamos "código vectorizado" dentro de cada paso temporal:
```python
for j in range(Nt):
    ut_int = u[j,1:-1]
    u_new = ut_int + k*vt
    vt = vt + k*A@ut_int
    u[j+1,1:-1] = u_new
```
Sin embargo, para la diferencia temporal de orden 2, hemos usado un bucle doble, que es más lento:
```python
for j in range(1, Nt):
    for a in range(1, Nx-1):
        u[j+1,a] = 2*(1-lamb2)*u[j,a]-u[j-1,a]+lamb2*(u[j,a-1]+u[j,a+1])
```

Reescribe este método usando un sólo bucle, que itera sobre el paso temporal, pero usando operaciones con arrays para las operaciones espaciales, como hicimos con el método de Euler.